In [1]:
import sys,importlib
sys.path.append('../')
import simulation
from numpy import *
import plotly.offline as py
import plotly.graph_objs as go

### sub-system

In [2]:
alpha = 1
delta = .25
gamma = .3
beta = -1
omega = 1
def dufffingOscillator(state,t):
    x,y = state[0],state[1]
    xdot = y
    ydot = -alpha*(x**3) - beta* x - delta*y + gamma*cos(omega*t)
    return asarray((xdot,ydot))

### coupling

In [15]:
a0,a1 = .5,.2
w = 1.3
epsilon = .00003

In [16]:
def coupling(stateA,stateB,t):
    x1,y1 = stateA
    x2,y2 = stateB
    #xdot = a1*w*x1*cos(w*t)+ y1*(a0+a1*sin(w*t)) -y2 -(x2-x1*(a0+a1*sin(w*t)))
    xdot = a1*w*x1*cos(w*t)# + (x2-x1*a1*sin(w*t))
    #ydot = a1*w*y1*cos(w*t) + alpha*x2**3 + beta*x2 + delta*y2 - gamma*cos(omega*t)+(a0+a1*sin(w*t))*(gamma*cos(omega*t)-alpha*x1**3-beta*x1-delta*y1) -(y2-y1*(a0+a1*sin(w*t)))
    ydot = (a1**3)*alpha*(x1**3)*(sin(w*t)**3) + a1*sin(w*t)*(beta*x1+delta*y1) + a1*w*y1*cos(w*t) + a1*sin(w*t)*(-alpha*x1**3-beta*x1-delta*y1+gamma*cos(omega*t)) - gamma*cos(omega*t) - (y2-y1*a1*sin(w*t))
    return asarray((xdot,ydot))

In [17]:
def coupling(stateA,stateB,t):
    x1,y1 = stateA
    x2,y2 = stateB
    xdot = a1*w*x1*cos(w*t) - y2 + y1*(a0+a1*sin(w*t))
    ydot = 0
    return asarray((xdot,ydot))

In [18]:
def stabilizer(stateA,stateB,t):
    x1,y1 = stateA
    x2,y2 = stateB
    xdot = epsilon + sin(w*t)
    ydot = 0
    return asarray((xdot,ydot))*(- x1*(a0 + a1*sin(w*t)) + x2)

### simulation

In [19]:
time = 10500
delTime = .1
tail = 10000
timeline = arange(0.0, time, delTime)

In [20]:
stateA0 = asarray([0.15,0.25])
stateB0 = asarray([1.5,0.34])
stateA,stateB = simulation.evolveAB(dufffingOscillator,dufffingOscillator,stateA0,stateB0,couplingB=coupling,stabilizerB=stabilizer,time=time,delTime=delTime,tail=tail)
timeline = timeline[-tail:]

### synchronization - order parameter

In [21]:
py.iplot([go.Scatter(x=timeline,y=stateB[:,0]/stateA[:,0])])

### eigenvalue evolution

In [22]:
def eigenvalueDirectional(stateA,stateB,t):
    value = epsilon 
    value += (epsilon + sin(w*t))*((a0 + a1*sin(w*t))**2)
    value += sin(w*t)
    return value

In [23]:
def eigenvalueSeparational(stateA,stateB,t):
    value = epsilon 
    value -= (a0 + a1*sin(w*t))*(a1*w*cos(w*t)-(a0+a1*sin(w*t))*(epsilon + sin(w*t)))
    value += sin(w*t)
    return value

In [24]:
py.iplot([go.Scatter(name='directional',x=timeline,y=eigenvalueDirectional(stateA,stateB,timeline)),
         go.Scatter(name='separational',x=timeline,y=eigenvalueDirectional(stateA,stateB,timeline))])

In [25]:
eigenvalueDirectional(stateA,stateB,timeline).mean()

0.10009729397485863

In [26]:
eigenvalueSeparational(stateA,stateB,timeline).mean()

0.1000368914407517

-----------------------------------------------